<figure>
<center> 
<h1><b>Evaluasi Akhir Semester Kapsel ILKOM</b></h1>
<h2>Oleh : Ario Fajar Pratama (06111640000087)</h2>
<img src='https://covid19.kemkes.go.id/wp-content/uploads/2020/04/banner.png'/> </center>
</figure>


# <h2><b><i>Import Library</i> yang diperlukan dalam program ini</b></h2>

In [0]:
# Packages / libraries
import os 
import numpy as np 
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
import datetime    
from matplotlib import pyplot as plt
import seaborn as sns
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, explained_variance_score, mean_absolute_error, mean_squared_error
from math import sqrt
from datetime import datetime
from jinja2 import Template
from IPython.display import HTML

%matplotlib inline

# Mengubah angka Scientific ke float
#np.set_printoptions(formatter={'float_kind':'{:f}'.format})

# meningkatkan ukuran dari sns plots
#sns.set(rc={'figure.figsize':(12,10)})

# <h2>Mengimport Data COVID-19 yang dapat diunduh di <a href="https://github.com/CSSEGISandData/COVID-19/tree/master/csse_covid_19_data/csse_covid_19_time_series"> <i>Link</i> ini </a></h2>

In [0]:
# Memuat Data mentah
data_mentah_confirmed = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
data_mentah_deaths = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
data_mentah_recovered = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')

# Menampilkan ukuran dari data mentah di atas
print("Ukuran Data Confirmed Adalah : ", data_mentah_confirmed.shape, "--> (Baris, Kolom)")
print("Ukuran Data Deaths Adalah    : ", data_mentah_deaths.shape, "--> (Baris, Kolom)")
print("Ukuran Data Recovered Adalah : ", data_mentah_recovered.shape, "--> (Baris, Kolom)")

Ukuran Data Confirmed Adalah :  (266, 130) --> (Baris, Kolom)
Ukuran Data Deaths Adalah    :  (266, 130) --> (Baris, Kolom)
Ukuran Data Recovered Adalah :  (253, 130) --> (Baris, Kolom)


In [0]:
# Menampilkan Salah satu Data Mentah di atas, yaitu Data Mentah Confirmed
data_mentah_confirmed

Province/State         Country/Region        Lat  ...  5/24/20  5/25/20  5/26/20
0              NaN            Afghanistan  33.000000  ...    10582    11173    11831
1              NaN                Albania  41.153300  ...      998     1004     1029
2              NaN                Algeria  28.033900  ...     8306     8503     8697
3              NaN                Andorra  42.506300  ...      762      763      763
4              NaN                 Angola -11.202700  ...       69       70       70
..             ...                    ...        ...  ...      ...      ...      ...
261            NaN  Sao Tome and Principe   0.186360  ...      251      299      441
262            NaN                  Yemen  15.552727  ...      222      233      249
263            NaN                Comoros -11.645500  ...       87       87       87
264            NaN             Tajikistan  38.861034  ...     2929     3100     3266
265            NaN                Lesotho -29.609988  ...        2        2        2

[266 rows x 130 columns]

# <h2><b>Mengubah ukuran dari Data Mentah di atas</b></h2>

In [0]:
# Menentukan Kolom fitur dari data mentah
fitur = ['Province/State', 'Country/Region', 'Lat', 'Long']

# Mengubah ukuran dari data tabel mentah dan menambahkan kolom secara berturut-turut 'Confirmed', 'Deaths', dan 'Recovered' 
# pada masing-masing Data
data_pivot_confirmed = pd.melt(data_mentah_confirmed, id_vars=fitur, var_name=['Date'], value_name ='Confirmed')
data_pivot_deaths = pd.melt(data_mentah_deaths, id_vars=fitur, var_name=['Date'], value_name ='Deaths')
data_pivot_recovered = pd.melt(data_mentah_recovered, id_vars=fitur, var_name=['Date'], value_name ='Recovered')

# Menampilkan ukuran dari data tabel mentah yang sudah diubah ukurannya
print("Ukuran data Confirmed menjadi :", data_pivot_confirmed.shape, "--> (Baris, Kolom)")
print("Ukuran data Deaths menjadi    :", data_pivot_deaths.shape, "--> (Baris, Kolom)")
print("Ukuran data Recovered menjadi :", data_pivot_recovered.shape, "--> (Baris, Kolom)")

Ukuran data Confirmed menjadi : (33516, 6) --> (Baris, Kolom)
Ukuran data Deaths menjadi    : (33516, 6) --> (Baris, Kolom)
Ukuran data Recovered menjadi : (31878, 6) --> (Baris, Kolom)


In [0]:
# Menampilkan Salah satu hasil Data Mentah yang telah diubah ukurannya, yaitu Data Pivot Confirmed
data_pivot_recovered

Province/State         Country/Region  ...     Date  Recovered
0                NaN            Afghanistan  ...  1/22/20          0
1                NaN                Albania  ...  1/22/20          0
2                NaN                Algeria  ...  1/22/20          0
3                NaN                Andorra  ...  1/22/20          0
4                NaN                 Angola  ...  1/22/20          0
...              ...                    ...  ...      ...        ...
31873            NaN  Sao Tome and Principe  ...  5/26/20         68
31874            NaN                  Yemen  ...  5/26/20         10
31875            NaN                Comoros  ...  5/26/20         21
31876            NaN             Tajikistan  ...  5/26/20       1417
31877            NaN                Lesotho  ...  5/26/20          0

[31878 rows x 6 columns]

# <h2><b>Mengganti format data pada kolom 'Date' menjadi format datetime (yyyy-dd-mm)</b></h2>

In [0]:
# Mengubah format pada kolom 'Date' menjadi format datetime (yyyy-dd-mm)
data_pivot_confirmed['Date'] = pd.to_datetime(data_pivot_confirmed['Date'])
data_pivot_deaths['Date'] = pd.to_datetime(data_pivot_deaths['Date'])
data_pivot_recovered['Date'] = pd.to_datetime(data_pivot_recovered['Date'])

# Menampilkan salah satu data yaitu Data Confirmed setelah format pada kolom 'Date' diganti
data_pivot_confirmed

Province/State         Country/Region  ...       Date  Confirmed
0                NaN            Afghanistan  ... 2020-01-22          0
1                NaN                Albania  ... 2020-01-22          0
2                NaN                Algeria  ... 2020-01-22          0
3                NaN                Andorra  ... 2020-01-22          0
4                NaN                 Angola  ... 2020-01-22          0
...              ...                    ...  ...        ...        ...
33511            NaN  Sao Tome and Principe  ... 2020-05-26        441
33512            NaN                  Yemen  ... 2020-05-26        249
33513            NaN                Comoros  ... 2020-05-26         87
33514            NaN             Tajikistan  ... 2020-05-26       3266
33515            NaN                Lesotho  ... 2020-05-26          2

[33516 rows x 6 columns]

# <h2><b>Mengatasi Cell pada tiap data yang bernilai Null atau NaN</b></h2>

In [0]:
# Menyelidiki dan menampilkan semua data pada tiap kolom yang bernilai null
print("DATA CONFIRMED\n", data_pivot_confirmed.isnull().sum())
print("\nDATA DEATHS\n", data_pivot_deaths.isnull().sum())
print("\nDATA RECOVERED\n", data_pivot_recovered.isnull().sum())

DATA CONFIRMED
 Province/State    23310
Country/Region        0
Lat                   0
Long                  0
Date                  0
Confirmed             0
dtype: int64

DATA DEATHS
 Province/State    23310
Country/Region        0
Lat                   0
Long                  0
Date                  0
Deaths                0
dtype: int64

DATA RECOVERED
 Province/State    23436
Country/Region        0
Lat                   0
Long                  0
Date                  0
Recovered             0
dtype: int64


In [0]:
# Mengatasi nilai null pada kolom 'Province/State' dengan cara mengisi cell tsb dengan isi cell pada kolom 'Country/Region'
data_pivot_confirmed['Province/State'].fillna(data_pivot_confirmed['Country/Region'], inplace=True)
data_pivot_deaths['Province/State'].fillna(data_pivot_deaths['Country/Region'], inplace=True)
data_pivot_recovered['Province/State'].fillna(data_pivot_recovered['Country/Region'], inplace=True)

# Menampilkan hasil dari diatasi nilai null pada kolom 'Province/State' dari salah satu data yaitu data confirmed
data_pivot_confirmed  

Province/State         Country/Region  ...       Date  Confirmed
0                Afghanistan            Afghanistan  ... 2020-01-22          0
1                    Albania                Albania  ... 2020-01-22          0
2                    Algeria                Algeria  ... 2020-01-22          0
3                    Andorra                Andorra  ... 2020-01-22          0
4                     Angola                 Angola  ... 2020-01-22          0
...                      ...                    ...  ...        ...        ...
33511  Sao Tome and Principe  Sao Tome and Principe  ... 2020-05-26        441
33512                  Yemen                  Yemen  ... 2020-05-26        249
33513                Comoros                Comoros  ... 2020-05-26         87
33514             Tajikistan             Tajikistan  ... 2020-05-26       3266
33515                Lesotho                Lesotho  ... 2020-05-26          2

[33516 rows x 6 columns]

# <h2><b>Menggabungkan 3 Data menjadi 1 data tabel</b></h2>

In [0]:
# Menggabungkan Data Confirmed dengan Data Deaths dengan nama 'data_join'
data_join = data_pivot_confirmed.merge(data_pivot_deaths.drop(['Lat', 'Long'], axis=1), 
                                      how = 'left', 
                                      left_on = ['Province/State','Country/Region','Date'], 
                                      right_on = ['Province/State','Country/Region','Date']
)

# Menampilkan hasil ukuran gabungan Data Confirmed dengan Data Deaths
print("Ukuran Gabungan Data Confirmed & Data Deaths           : ", data_join.shape)

# Menggabungkan Data 'data_join' dengan Data Recovered dan memberi nama 'data_join' lagi
# atau dapat diartikan data 'full_join' pada sebelumnya akan ditimpa dengan gabungan data 'full_join' dan data recovered 
data_join = data_join.merge(data_pivot_recovered.drop(['Lat', 'Long'], axis=1), 
                                      how = 'left', 
                                      left_on = ['Province/State','Country/Region','Date'], 
                                      right_on = ['Province/State','Country/Region','Date']
)

# Menampilkan hasil ukuran gabungan Data Confirmed, Data Deaths dan Data Recovered
print("Ukuran Gabungan Data Confirmed, Deaths, dan Recovered  : ", data_join.shape)

Ukuran Gabungan Data Confirmed & Data Deaths           :  (33516, 7)
Ukuran Gabungan Data Confirmed, Deaths, dan Recovered  :  (33516, 8)


In [0]:
# Mengecek nilai Null atau NaN pada data gabungan
# Potensi terbesar kolom yang bernilai Null atau NaN adalah kolom 'Confirmed', 'Deaths', dan 'Recovered'
# Hal ini dikarenakan 3 kolom tersebut tidak menjadi pivot/key/id dalam proses penggabungan
data_join.isnull().sum()

Province/State       0
Country/Region       0
Lat                  0
Long                 0
Date                 0
Confirmed            0
Deaths               0
Recovered         1764
dtype: int64

In [0]:
# Mengubah Nilai Null atau NaN pada gabungan menjadi nilai 0
kolom_target = ['Confirmed', 'Deaths', 'Recovered']
data_join[kolom_target] = np.nan_to_num(data_join[kolom_target])
data_join.isnull().sum()

Province/State    0
Country/Region    0
Lat               0
Long              0
Date              0
Confirmed         0
Deaths            0
Recovered         0
dtype: int64

In [0]:
# Menampilkan Hasil Gabungan Data
data_join

Province/State         Country/Region  ...  Deaths  Recovered
0                Afghanistan            Afghanistan  ...     0.0        0.0
1                    Albania                Albania  ...     0.0        0.0
2                    Algeria                Algeria  ...     0.0        0.0
3                    Andorra                Andorra  ...     0.0        0.0
4                     Angola                 Angola  ...     0.0        0.0
...                      ...                    ...  ...     ...        ...
33511  Sao Tome and Principe  Sao Tome and Principe  ...    12.0       68.0
33512                  Yemen                  Yemen  ...    49.0       10.0
33513                Comoros                Comoros  ...     1.0       21.0
33514             Tajikistan             Tajikistan  ...    47.0     1417.0
33515                Lesotho                Lesotho  ...     0.0        0.0

[33516 rows x 8 columns]

# <h2><b>Menambahkan beberapa kolom data sebagai pendukung informasi </b></h2>


<center>

<h3><b>Active = Confirmed - Deaths - Recovered</b></h3></center>

In [0]:
# Menambahkan kolom 'Active' dan mengubah nilai kolom 'Active' jika bernilai negatif dengan nilai 0
data_join['Active'] = [0 if i < 0 else i for i in (data_join['Confirmed'] - data_join['Deaths'] - data_join['Recovered'])]

In [0]:
# Menambahkan Kolom'Confirmed-1', 'Deaths-1', 'Recovered-1', 'Active-1',
# 'Confirmed Daily', 'Deaths Daily', 'Recovered Daily', dan 'Active Daily'
temp_data_join = data_join.copy()
temp_data_join['Date copy'] = temp_data_join['Date'] + pd.Timedelta(days=1)
temp_data_join.rename(columns={'Confirmed': 'Confirmed-1', 'Deaths': 'Deaths-1', 'Recovered': 'Recovered-1', 'Active': 'Active-1',
                          'Date': 'Date-1'}, inplace=True)
data_join = data_join.merge(temp_data_join[['Province/State', 'Country/Region', 'Date-1','Confirmed-1', 'Deaths-1', 
                            'Recovered-1', 'Active-1', 'Date copy']], how = 'left',
                             left_on = ['Province/State','Country/Region','Date'], 
                             right_on = ['Province/State', 'Country/Region','Date copy'])

data_join['Confirmed Daily'] = data_join['Confirmed'] - data_join['Confirmed-1']
data_join['Deaths Daily'] = data_join['Deaths'] - data_join['Deaths-1']
data_join['Recovered Daily'] = data_join['Recovered'] - data_join['Recovered-1']
data_join['Active Daily'] = data_join['Active'] - data_join['Active-1']

# Mengecek Nilai Null atau NaN pada data yang sudah ditambahkan kolom
data_join.isnull().sum()

Province/State       0
Country/Region       0
Lat                  0
Long                 0
Date                 0
Confirmed            0
Deaths               0
Recovered            0
Active               0
Date-1             266
Confirmed-1        266
Deaths-1           266
Recovered-1        266
Active-1           266
Date copy          266
Confirmed Daily    266
Deaths Daily       266
Recovered Daily    266
Active Daily       266
dtype: int64

In [0]:
# Menghapus Kolom 'Date copy'
del data_join['Date copy']

# Memberi value pada kolom 'Date Day-1' dengan cara kolom 'Date' dikurangi 1 hari
data_join['Date-1'] = data_join['Date'] - pd.Timedelta(days=1)

# Mengatasi Nilai Null atau NaN pada data gabungan
kolom_target = ['Confirmed-1', 'Deaths-1', 'Recovered-1', 'Active-1',
                'Confirmed Daily', 'Deaths Daily', 'Recovered Daily', 'Active Daily']
data_join[kolom_target] = np.nan_to_num(data_join[kolom_target])
data_join.isnull().sum()

Province/State     0
Country/Region     0
Lat                0
Long               0
Date               0
Confirmed          0
Deaths             0
Recovered          0
Active             0
Date-1             0
Confirmed-1        0
Deaths-1           0
Recovered-1        0
Active-1           0
Confirmed Daily    0
Deaths Daily       0
Recovered Daily    0
Active Daily       0
dtype: int64

In [0]:
# Mengubah tipe dan format kolom 'Date dari tipe datetime (mm-dd-yyyy) menjadi tipe str (dd-mm-yyyy)
data_join['Date'] = [date_obj.strftime('%d-%m-%Y') for date_obj in data_join['Date']]
data_join['Date-1'] = [date_obj.strftime('%d-%m-%Y') for date_obj in data_join['Date-1']]

# Menampilkan hasil data gabungan
data_join

Province/State  ... Active Daily
0                Afghanistan  ...          0.0
1                    Albania  ...          0.0
2                    Algeria  ...          0.0
3                    Andorra  ...          0.0
4                     Angola  ...          0.0
...                      ...  ...          ...
33511  Sao Tome and Principe  ...         77.0
33512                  Yemen  ...         11.0
33513                Comoros  ...          0.0
33514             Tajikistan  ...        143.0
33515                Lesotho  ...          0.0

[33516 rows x 18 columns]

# <h2><b>Peta Persebaran Virus COVID-19 di Seluruh Dunia </b></h2>

In [0]:
# Peta persebaran virus Covid-19 dari waktu ke waktu (time series)

pio.templates['shahin'] = pio.to_templated(go.Figure().update_layout(
    legend=dict(orientation="h",y=1.1, x=.5, xanchor='center'),
    margin=dict(t=0,r=0,b=0,l=0))).layout.template
pio.templates.default = 'shahin'

access_token = 'pk.eyJ1IjoiYXJpb2ZhamFyIiwiYSI6ImNrMGU0bmd5dDA2ZDIzY2tmM2J3cXo0emkifQ.wbo63eCt71Mrbjfr1tugAw'
px.set_mapbox_access_token(access_token)

date_mask = data_join['Date'] == data_join['Date'].max()

fig = px.scatter_mapbox(
    data_join, lat="Lat", lon="Long",
    size="Active", size_max=50,
    color="Deaths", color_continuous_scale=px.colors.sequential.Pinkyl,
    hover_name="Province/State",           
    mapbox_style='dark', zoom=1,
    animation_frame="Date", animation_group="Province/State"
)
fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 250
fig.layout.updatemenus[0].buttons[0].args[1]["transition"]["duration"] = 250
fig.layout.coloraxis.showscale = False
fig.layout.sliders[0].pad.t = 10
fig.layout.updatemenus[0].pad.t= 10

fig.show()

In [0]:
# Peta persebaran virus COVID-19 pada waktu terupdate
date = pd.to_datetime(data_join['Date'], format='%d-%m-%Y')
waktu_update = max(date).strftime('%d-%m-%Y')

data = data_join[data_join['Date']==waktu_update]
colors = ["orange","lightseagreen", "crimson"]
ket = {1:'Update Confirmed', 2:'Update Recovered',3:'Update Deaths'}
nama = {1:'Confirmed', 2:'Recovered', 3:'Deaths'}
fig = go.Figure()

for i in range(1,4) :
    df_data = data[fitur + [nama[i]]]
    fig.add_trace(go.Scattergeo(
            lon = df_data['Long'],
            lat = df_data['Lat'],
            text = df_data['Province/State'] + '<br>Total =' + (df_data[nama[i]]).astype(str),
            name = nama[i],
            marker = dict(
                size = df_data[nama[i]]/200,
                color = colors[i-1],
                line_color='rgb(40,40,40)',
                line_width=0.5,
                sizemode = 'area'
            )))

fig.update_layout(
    title = go.layout.Title(
        text = 'Geographic distribution of COVID-19<br>cases worldwide, as of ' + waktu_update),
    geo = dict(

            #landcolor = 'rgb(217, 217, 217)',
            showland=True, landcolor="LightGreen",
            showocean=True, oceancolor="LightBlue",
            showlakes=True, lakecolor="Blue",
            showrivers=True, rivercolor="Blue"
          
        ),
        yaxis=dict(
        range=[200, 200]
    ),
    xaxis=dict(
        range=[200, 200]
    ),
     autosize=True,
    hovermode='closest',
    
    legend_traceorder = 'reversed'
)

fig.show()

# <h2><b>Membuat Tabel Data untuk setiap negara </b></h2>

In [0]:
# Menghitung selisih hari
jarak_waktu = (max(date)-min(date)).days+1

# Membagi data dengan negara yang memiliki beberapa provinsi dan memiliki 1 provinsi
index, counts = np.unique(data_join['Country/Region'].values,return_counts=True)
Data_Negara = pd.DataFrame({'Country/Region':index, 'Freq':counts/jarak_waktu})
negara_sama_dengan_1 = pd.DataFrame(Data_Negara[Data_Negara['Freq'] == 1]).reset_index().drop(['index'], axis=1)
negara_lebih_dari_1 = pd.DataFrame(Data_Negara[Data_Negara['Freq'] > 1]).reset_index().drop(['index'], axis=1)

# menampilkan data dengan negara yang memiliki satu provinsi
negara_sama_dengan_1

Country/Region  Freq
0           Afghanistan   1.0
1               Albania   1.0
2               Algeria   1.0
3               Andorra   1.0
4                Angola   1.0
..                  ...   ...
176  West Bank and Gaza   1.0
177      Western Sahara   1.0
178               Yemen   1.0
179              Zambia   1.0
180            Zimbabwe   1.0

[181 rows x 2 columns]

In [0]:
# menampilkan data dengan negara yang memiliki beberapa provinsi
negara_lebih_dari_1

Country/Region  Freq
0       Australia   8.0
1          Canada  14.0
2           China  33.0
3         Denmark   3.0
4          France  11.0
5     Netherlands   5.0
6  United Kingdom  11.0

In [0]:
# Menjumlahkan tiap kasus dari negara yang memiliki beberapa provinsi
join_negara = data_join.loc[data_join['Country/Region'].isin(negara_lebih_dari_1['Country/Region'])]
join_negara = join_negara.drop(['Province/State', 'Lat', 'Long', 'Date-1'], axis=1)
banyak_date = join_negara['Date'].unique()
tampung = []
for i in banyak_date:
    result = join_negara[join_negara['Date'] == i]
    for j in negara_lebih_dari_1['Country/Region']:
        temp = np.array([j, i])
        total = np.append(temp, result[result['Country/Region']==j].drop(['Country/Region', 'Date'], axis=1).sum().values)
        tampung.append(total)
tampung = pd.DataFrame(tampung, columns=['Country/Region', 'Date', 'Confirmed', 'Deaths', 'Recovered', 'Active']+kolom_target)

# Menampilkan hasil penjumlahan tiap kasus dari negara yang memiliki beberapa provinsi
tampung

Country/Region        Date  ... Recovered Daily Active Daily
0         Australia  22-01-2020  ...             0.0          0.0
1            Canada  22-01-2020  ...             0.0          0.0
2             China  22-01-2020  ...             0.0          0.0
3           Denmark  22-01-2020  ...             0.0          0.0
4            France  22-01-2020  ...             0.0          0.0
..              ...         ...  ...             ...          ...
877           China  26-05-2020  ...             6.0         -5.0
878         Denmark  26-05-2020  ...            80.0        -39.0
879          France  26-05-2020  ...           680.0       -973.0
880     Netherlands  26-05-2020  ...             0.0        107.0
881  United Kingdom  26-05-2020  ...             0.0       3915.0

[882 rows x 14 columns]

In [0]:
# Menggabungkan data hasil penjumlahan tiap kasus dari negara yang memiliki beberapa provinsi dengan negara yang lain
Data = data_join.loc[data_join['Country/Region'].isin(negara_sama_dengan_1['Country/Region'])].drop(['Province/State', 'Lat', 'Long', 'Date-1'], axis=1)
data_country = Data.append(tampung, ignore_index=True)

# Menampilkan hasil gabungan kasus dari tiap negara
#data_country['Continent'] = data_country['Country/Region'].map(mapping['map.continent'])
data_country[data_country['Country/Region']=='Brazil']

Country/Region        Date  ... Recovered Daily Active Daily
20            Brazil  22-01-2020  ...               0            0
201           Brazil  23-01-2020  ...               0            0
382           Brazil  24-01-2020  ...               0            0
563           Brazil  25-01-2020  ...               0            0
744           Brazil  26-01-2020  ...               0            0
...              ...         ...  ...             ...          ...
21921         Brazil  22-05-2020  ...            9470        10332
22102         Brazil  23-05-2020  ...            7157         8386
22283         Brazil  24-05-2020  ...            7324         7836
22464         Brazil  25-05-2020  ...            3922         6958
22645         Brazil  26-05-2020  ...            4760        10525

[126 rows x 14 columns]

# <h2><b>COVID-19 OVERVIEW</b></h2>

In [0]:
#hide
print('''
Example of using jupyter notebook, pandas (data transformations), jinja2 (html, visual)
to create visual dashboards with fastpages
You see also the live version on https://gramener.com/enumter/covid19/
''')


Example of using jupyter notebook, pandas (data transformations), jinja2 (html, visual)
to create visual dashboards with fastpages
You see also the live version on https://gramener.com/enumter/covid19/



In [0]:
base_url = 'https://raw.githubusercontent.com/pratapvardhan/notebooks/master/covid19/'
paths = {
    'mapping': base_url + 'mapping_countries.csv',
    'overview': base_url + 'overview.tpl'
}

def get_mappings(url):
    df = pd.read_csv(url)
    return {
        'df': df,
        'replace.country': dict(df.dropna(subset=['Name']).set_index('Country')['Name']),
        'map.continent': dict(df.set_index('Name')['Continent'])
    }

mapping = get_mappings(paths['mapping'])

def get_template(path):
    from urllib.parse import urlparse
    if bool(urlparse(path).netloc):
        from urllib.request import urlopen
        return urlopen(path).read().decode('utf8')
    return open(path).read()

def get_frame(name):
    url = (
        'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/'
        f'csse_covid_19_time_series/time_series_covid19_{name}_global.csv')
    df = pd.read_csv(url)
    # rename countries
    df['Country/Region'] = df['Country/Region'].replace(mapping['replace.country'])
    return df

def get_dates(df):
    dt_cols = df.columns[~df.columns.isin(['Province/State', 'Country/Region', 'Lat', 'Long'])]
    LAST_DATE_I = -1
    # sometimes last column may be empty, then go backwards
    for i in range(-1, -len(dt_cols), -1):
        if not df[dt_cols[i]].fillna(0).eq(0).all():
            LAST_DATE_I = i
            break
    return LAST_DATE_I, dt_cols

In [0]:
#hide
COL_REGION = 'Country/Region'
# Confirmed, Recovered, Deaths
df = get_frame('confirmed')
# dft_: timeseries, dfc_: today country agg
dft_cases = df
dft_deaths = get_frame('deaths')
dft_recovered = get_frame('recovered')
LAST_DATE_I, dt_cols = get_dates(df)

dt_today = dt_cols[LAST_DATE_I]
dt_5ago = dt_cols[LAST_DATE_I-5]


dfc_cases = dft_cases.groupby(COL_REGION)[dt_today].sum()
dfc_deaths = dft_deaths.groupby(COL_REGION)[dt_today].sum()
dfp_cases = dft_cases.groupby(COL_REGION)[dt_5ago].sum()
dfp_deaths = dft_deaths.groupby(COL_REGION)[dt_5ago].sum()

In [0]:
#hide
df_table = (pd.DataFrame(dict(Cases=dfc_cases, Deaths=dfc_deaths, PCases=dfp_cases, PDeaths=dfp_deaths))
             .sort_values(by=['Cases', 'Deaths'], ascending=[False, False])
             .reset_index())
df_table.rename(columns={'index': 'Country/Region'}, inplace=True)
for c in 'Cases, Deaths'.split(', '):
    df_table[f'{c} (+)'] = (df_table[c] - df_table[f'P{c}']).clip(0)  # DATA BUG
df_table['Fatality Rate'] = (100 * df_table['Deaths'] / df_table['Cases']).round(1)
df_table['Continent'] = df_table['Country/Region'].map(mapping['map.continent'])
df_table.head(15)

Country/Region    Cases  Deaths  ...  Deaths (+)  Fatality Rate      Continent
0               US  1680913   98913  ...        4211            5.9  North America
1           Brazil   391222   24512  ...        4465            6.3  South America
2           Russia   362342    3807  ...         708            1.1         Europe
3   United Kingdom   266599   37130  ...        1006           13.9         Europe
4            Spain   236259   27117  ...           0           11.5         Europe
5            Italy   230555   32955  ...         469           14.3         Europe
6           France   182847   28533  ...         315           15.6         Europe
7          Germany   181200    8372  ...         169            4.6         Europe
8           Turkey   158762    4397  ...         148            2.8           Asia
9            India   150793    4344  ...         760            2.9           Asia
10            Iran   139511    7508  ...         259            5.4           Asia
11            Peru   129751    3788  ...         640            2.9  South America
12          Canada    88090    6753  ...         486            7.7  North America
13           China    84103    4638  ...           0            5.5           Asia
14           Chile    77961     806  ...         217            1.0  South America

[15 rows x 9 columns]

In [0]:
#hide
#delete problematic countries from table
df_table = df_table[~df_table['Country/Region'].isin(['Cape Verde', 'Cruise Ship', 'Kosovo'])]

In [0]:
#hide
# world, china, europe, us
metrics = ['Cases', 'Deaths', 'Cases (+)', 'Deaths (+)']
s_china = df_table[df_table['Country/Region'].eq('China')][metrics].sum().add_prefix('China ')
s_us = df_table[df_table['Country/Region'].eq('US')][metrics].sum().add_prefix('US ')
s_eu = df_table[df_table['Continent'].eq('Europe')][metrics].sum().add_prefix('EU ')
summary = {'updated': pd.to_datetime(dt_today), 'since': pd.to_datetime(dt_5ago)}
summary = {**summary, **df_table[metrics].sum(), **s_china, **s_us, **s_eu}

In [0]:
#hide
dft_ct_cases = dft_cases.groupby(COL_REGION)[dt_cols].sum()
dft_ct_new_cases = dft_ct_cases.diff(axis=1).fillna(0).astype(int)

In [0]:
#hide_input
template = Template(get_template(paths['overview']))
html = template.render(
    D=summary, table=df_table,  # REMOVE .head(20) to see all values
    newcases=dft_ct_new_cases.loc[:, dt_cols[LAST_DATE_I-jarak_waktu+1]:dt_cols[LAST_DATE_I]],
    np=np, pd=pd, enumerate=enumerate)
HTML(f'<div>{html}</div>')